In [1]:
import pandas as pd
import json
from datetime import datetime, timedelta
import warnings
import matplotlib.pyplot as plt
from matplotlib.dates import DateFormatter
import matplotlib.dates as mdates
warnings.filterwarnings(action='ignore')
pd.set_option('display.max_columns', None)

# Read the "acwr-data"

In [2]:
def load_and_feature_engineering_acwr(file_path):
    # read the data 
    acwr = pd.read_csv(file_path)
    # transform the date format
    for i, val in enumerate(acwr['date']):
        acwr['date'][i] = datetime.utcfromtimestamp(val)
    
    # drop the wellness data
    try:
        acwr = acwr.drop(columns=
                 ["fatigue","hydration","mood","nutrition","readiness",
                  "sleepduration","sleepquality","soreness","stress","total"], axis=1)
    except:
        acwr = acwr
    
    # transform the date type
    acwr['formatteddate'] = pd.to_datetime(acwr['date'])
    acwr["formatteddate_dt"] = pd.to_datetime(acwr["formatteddate"],format="%d/%m/%Y")
    acwr['formatteddate'] = acwr["formatteddate_dt"].astype(str)
    
    return acwr
    

In [3]:
file_path = "acwr_updated.csv"
acwr = load_and_feature_engineering_acwr(file_path)
acwr.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5292 entries, 0 to 5291
Data columns (total 13 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   acute             5292 non-null   float64       
 1   acwr              5292 non-null   float64       
 2   chronic           5292 non-null   float64       
 3   condition         5205 non-null   object        
 4   date              5292 non-null   object        
 5   duration          5292 non-null   int64         
 6   load              5292 non-null   int64         
 7   rpe               5292 non-null   int64         
 8   type              5205 non-null   object        
 9   player_id         5292 non-null   object        
 10  name              5292 non-null   object        
 11  formatteddate     5292 non-null   object        
 12  formatteddate_dt  5292 non-null   datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(3), object(6)
memory usage: 537.6+ KB


In [4]:
numerical = ['acute', 'acwr', 'chronic', 'duration', 'load','rpe']
categorical = ['condition', 'type'] 
na_cols = ["type","condition"]

In [5]:
acwr[acwr.isna().any(axis=1)]
#len(acwr[acwr.isna().any(axis=1)])
#35

acute      acwr     chronic condition                 date  \
3147  100.028229  1.943563   51.466417       NaN  2021-08-31 02:10:29   
3148  364.859214  1.171410  311.470227       NaN  2021-08-31 02:10:29   
3149  275.873053  1.687937  163.437967       NaN  2021-08-31 02:10:29   
3150  427.874266  1.318486  324.519490       NaN  2021-08-31 02:10:29   
3151  412.975247  1.299609  317.768832       NaN  2021-08-31 02:10:29   
...          ...       ...         ...       ...                  ...   
4590  311.801311  1.032951  301.854833       NaN  2021-12-09 04:46:12   
4591  340.585829  1.230432  276.801786       NaN  2021-12-09 04:46:12   
4592  319.912931  1.027532  311.341001       NaN  2021-12-09 04:46:12   
4593  294.441589  1.041749  282.641598       NaN  2021-12-09 04:46:12   
4594  408.879537  0.982701  416.077468       NaN  2021-12-09 04:46:12   

      duration  load  rpe type                 player_id             name  \
3147        60   300    5  NaN  5f0592e2239906121f930929      Kota Kawase   
3148        90   540    6  NaN  5f059326c37cc79a7d6a6ca9         james Ha   
3149        90   630    7  NaN  5f059355c37cc79a7d6a6caa       Jack Sealy   
3150        90   810    9  NaN  5f059378239906121f93092e       Xavi Cheng   
3151        90   810    9  NaN  5f059388239906121f93092f        Paco Chan   
...        ...   ...  ...  ...                       ...              ...   
4590        60   360    6  NaN  60f254fb854df5b9da1bac56  LucianoDa Silva   
4591        60   420    7  NaN  6107d0a36f7b01ca9c0f6571        ChanKa Po   
4592        60   360    6  NaN  61139a2f859c5efc737749ba       Ju Yingzhi   
4593        60   360    6  NaN  611a41e057d5db652811c0f3    ChenChin Lung   
4594        90   450    5  NaN  6153f4f14983cc4b427f2af2          Ivan Ng   

            formatteddate    formatteddate_dt  
3147  2021-08-31 02:10:29 2021-08-31 02:10:29  
3148  2021-08-31 02:10:29 2021-08-31 02:10:29  
3149  2021-08-31 02:10:29 2021-08-31 02:10:29  
3150  2021-08-31 02:10:29 2021-08-31 02:10:29  
3151  2021-08-31 02:10:29 2021-08-31 02:10:29  
...                   ...                 ...  
4590  2021-12-09 04:46:12 2021-12-09 04:46:12  
4591  2021-12-09 04:46:12 2021-12-09 04:46:12  
4592  2021-12-09 04:46:12 2021-12-09 04:46:12  
4593  2021-12-09 04:46:12 2021-12-09 04:46:12  
4594  2021-12-09 04:46:12 2021-12-09 04:46:12  

[87 rows x 13 columns]

In [6]:
#impute the missing 'condition' and 'type' with the most frequent values
acwr1 = acwr.fillna(acwr.mode().iloc[0])
acwr1

acute      acwr     chronic         condition                date  \
0     180.000000  1.000000  180.000000  Artificial (Dry) 2020-06-29 00:00:00   
1     325.000000  1.000000  325.000000  Artificial (Dry) 2020-06-29 00:00:00   
2     390.000000  1.000000  390.000000  Artificial (Dry) 2020-06-29 00:00:00   
3     325.000000  1.000000  325.000000  Artificial (Dry) 2020-06-29 00:00:00   
4     195.000000  1.000000  195.000000  Artificial (Dry) 2020-06-29 00:00:00   
...          ...       ...         ...               ...                 ...   
5287   87.924115  0.514831  170.782587             Mixed 2022-02-04 05:59:59   
5288  145.724642  0.652914  223.191242             Mixed 2022-02-04 05:59:59   
5289  134.414729  0.724831  185.442837             Mixed 2022-02-04 05:59:59   
5290   91.835734  0.577736  158.958055             Mixed 2022-02-04 05:59:59   
5291  132.608956  0.682794  194.215144             Mixed 2022-02-04 05:59:59   

      duration  load  rpe              type                 player_id  \
0           45   180    4  Practice (Field)  5f014aa4b8bec1cf08f7ca0f   
1           65   325    5  Practice (Field)  5f0592cc239906121f930928   
2           65   390    6  Practice (Field)  5f0592e2239906121f930929   
3           65   325    5  Practice (Field)  5f059326c37cc79a7d6a6ca9   
4           65   195    3  Practice (Field)  5f059355c37cc79a7d6a6caa   
...        ...   ...  ...               ...                       ...   
5287        40   120    3  Quarantine - Run  60f254d8a1b3ec106cc401da   
5288        40   240    6  Quarantine - Run  60f254fb854df5b9da1bac56   
5289        40   240    6  Quarantine - Run  6107d0a36f7b01ca9c0f6571   
5290        40   200    5  Quarantine - Run  61139a2f859c5efc737749ba   
5291        40   240    6  Quarantine - Run  611a41e057d5db652811c0f3   

                 name        formatteddate    formatteddate_dt  
0         Zesh Rehman  2020-06-29 00:00:00 2020-06-29 00:00:00  
1          TszTo Choy  2020-06-29 00:00:00 2020-06-29 00:00:00  
2         Kota Kawase  2020-06-29 00:00:00 2020-06-29 00:00:00  
3            james Ha  2020-06-29 00:00:00 2020-06-29 00:00:00  
4          Jack Sealy  2020-06-29 00:00:00 2020-06-29 00:00:00  
...               ...                  ...                 ...  
5287    Khan Jahangir  2022-02-04 05:59:59 2022-02-04 05:59:59  
5288  LucianoDa Silva  2022-02-04 05:59:59 2022-02-04 05:59:59  
5289        ChanKa Po  2022-02-04 05:59:59 2022-02-04 05:59:59  
5290       Ju Yingzhi  2022-02-04 05:59:59 2022-02-04 05:59:59  
5291    ChenChin Lung  2022-02-04 05:59:59 2022-02-04 05:59:59  

[5292 rows x 13 columns]

In [12]:
set(acwr[acwr["type"]=="Game"]["condition"])

{'Artificial (Dry)', 'Artificial (Wet)', 'Grass (Dry)', 'Grass (Wet)'}

In [13]:
set(acwr[acwr["type"]!="Game"]["condition"])

{'Artificial (Dry)',
 'Artificial (Wet)',
 'Grass (Dry)',
 'Grass (Wet)',
 'Gym/Indoors',
 'Hike',
 'Mixed',
 'Track',
 nan}

In [232]:
players = set(acwr["player_id"])

In [233]:
len(players)

21

# Read the "injurcsv"

In [7]:
def load_and_feature_engineering_injury(file_path):
    injury = pd.read_csv(file_path)
    for i, val in enumerate(injury['Injury Date']):
        injury['Injury Date'][i] = datetime.utcfromtimestamp(val)
    for i, val in enumerate(injury['Return Date']):
        injury['Return Date'][i] = datetime.utcfromtimestamp(val)
    
    injury['Injury Date'] = pd.to_datetime(injury['Injury Date'])#.dt.date()
    injury['Return Date'] = pd.to_datetime(injury['Return Date'])

    injury['FormattedInjuryDate'] = injury['Injury Date'].dt.date.astype(str)
    injury['FormattedReturnDate'] = injury['Return Date'].dt.date.astype(str)

    injury['FormattedInjuryDate_dt'] = pd.to_datetime(injury['FormattedInjuryDate'])
    injury['FormattedReturnDate_dt'] = pd.to_datetime(injury['FormattedReturnDate']) 
                                       
                                       
    injury = injury.drop(['Diagnosis','Notes'], axis=1)
    chronic_injury = injury[injury['Onset'] != 'Acute']
    return injury, chronic_injury

In [8]:
file_path = "injury_updated.csv"
injury, chronic_injury = load_and_feature_engineering_injury(file_path)

In [9]:
print(injury.info())
print(chronic_injury.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41 entries, 0 to 40
Data columns (total 16 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   Activity                40 non-null     object        
 1   Classification          41 non-null     object        
 2   Injury Date             41 non-null     datetime64[ns]
 3   Location                39 non-null     object        
 4   OSIICs                  16 non-null     object        
 5   Onset                   41 non-null     object        
 6   Past Injury             41 non-null     object        
 7   Reoccurance             34 non-null     object        
 8   Return Date             41 non-null     datetime64[ns]
 9   Side                    38 non-null     object        
 10  Surgery                 41 non-null     object        
 11  u_id                    41 non-null     object        
 12  FormattedInjuryDate     41 non-null     object      

# Merge the acwr and injury data

In [14]:
outer_df = pd.merge(acwr1, injury,  
                        how='outer', left_on=['player_id','formatteddate'], right_on = ['u_id','FormattedInjuryDate'])

In [15]:
outer_df.shape

(5333, 29)

In [16]:
outer_df

acute  acwr  chronic         condition       date  duration   load  rpe  \
0     180.0   1.0    180.0  Artificial (Dry) 2020-06-29      45.0  180.0  4.0   
1     325.0   1.0    325.0  Artificial (Dry) 2020-06-29      65.0  325.0  5.0   
2     390.0   1.0    390.0  Artificial (Dry) 2020-06-29      65.0  390.0  6.0   
3     325.0   1.0    325.0  Artificial (Dry) 2020-06-29      65.0  325.0  5.0   
4     195.0   1.0    195.0  Artificial (Dry) 2020-06-29      65.0  195.0  3.0   
...     ...   ...      ...               ...        ...       ...    ...  ...   
5328    NaN   NaN      NaN               NaN        NaT       NaN    NaN  NaN   
5329    NaN   NaN      NaN               NaN        NaT       NaN    NaN  NaN   
5330    NaN   NaN      NaN               NaN        NaT       NaN    NaN  NaN   
5331    NaN   NaN      NaN               NaN        NaT       NaN    NaN  NaN   
5332    NaN   NaN      NaN               NaN        NaT       NaN    NaN  NaN   

                  type                 player_id         name  \
0     Practice (Field)  5f014aa4b8bec1cf08f7ca0f  Zesh Rehman   
1     Practice (Field)  5f0592cc239906121f930928   TszTo Choy   
2     Practice (Field)  5f0592e2239906121f930929  Kota Kawase   
3     Practice (Field)  5f059326c37cc79a7d6a6ca9     james Ha   
4     Practice (Field)  5f059355c37cc79a7d6a6caa   Jack Sealy   
...                ...                       ...          ...   
5328               NaN                       NaN          NaN   
5329               NaN                       NaN          NaN   
5330               NaN                       NaN          NaN   
5331               NaN                       NaN          NaN   
5332               NaN                       NaN          NaN   

            formatteddate formatteddate_dt               Activity  \
0     2020-06-29 00:00:00       2020-06-29                    NaN   
1     2020-06-29 00:00:00       2020-06-29                    NaN   
2     2020-06-29 00:00:00       2020-06-29                    NaN   
3     2020-06-29 00:00:00       2020-06-29                    NaN   
4     2020-06-29 00:00:00       2020-06-29                    NaN   
...                   ...              ...                    ...   
5328                  NaN              NaT            Competition   
5329                  NaN              NaT            Competition   
5330                  NaN              NaT       General Training   
5331                  NaN              NaT            Competition   
5332                  NaN              NaT  Not Related to Sports   

        Classification         Injury Date                Location OSIICs  \
0                  NaN                 NaT                     NaN    NaN   
1                  NaN                 NaT                     NaN    NaN   
2                  NaN                 NaT                     NaN    NaN   
3                  NaN                 NaT                     NaN    NaN   
4                  NaN                 NaT                     NaN    NaN   
...                ...                 ...                     ...    ...   
5328        New Injury 2021-11-20 10:12:50  Competition - Domestic    NaN   
5329  Recurrent Injury 2021-11-20 10:15:35  Competition - Domestic    NaN   
5330  Recurrent Injury 2021-11-29 06:29:03          DTE - Domestic    NaN   
5331        New Injury 2022-01-02 05:45:26  Competition - Domestic    NaN   
5332        New Injury 2022-01-19 05:44:10                   Other    NaN   

      Onset Past Injury     Reoccurance         Return Date   Side Surgery  \
0       NaN         NaN             NaN                 NaT    NaN     NaN   
1       NaN         NaN             NaN                 NaT    NaN     NaN   
2       NaN         NaN             NaN                 NaT    NaN     NaN   
3       NaN         NaN             NaN                 NaT    NaN     NaN   
4       NaN         NaN             NaN                 NaT    NaN     NaN   
...     ...         ...       

In [63]:
outer_df[outer_df['u_id']=='5f0592e2239906121f930929']

acute  acwr  chronic    condition                date  duration   load  \
2176  468.0  1.27    368.0  Grass (Wet) 2021-02-27 15:34:55      95.0  950.0   
2727  276.0  0.85    326.0  Grass (Wet) 2021-04-27 06:07:50      63.0  378.0   
3466    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   
3467    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   
3468    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   
3469    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   
3470    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   
3471    NaN   NaN      NaN          NaN                 NaT       NaN    NaN   

       rpe              type                 player_id         name  \
2176  10.0              Game  5f0592e2239906121f930929  Kota Kawase   
2727   6.0  Practice (Field)  5f0592e2239906121f930929  Kota Kawase   
3466   NaN               NaN                       NaN          NaN   
3467   NaN               NaN                       NaN          NaN   
3468   NaN               NaN                       NaN          NaN   
3469   NaN               NaN                       NaN          NaN   
3470   NaN               NaN                       NaN          NaN   
3471   NaN               NaN                       NaN          NaN   

     formatteddate formatteddate_dt     Activity    Classification  \
2176    2021-02-27       2021-02-27  Competition  Recurrent Injury   
2727    2021-04-27       2021-04-27  Competition        New Injury   
3466           NaN              NaT  Competition        New Injury   
3467           NaN              NaT        Other  Recurrent Injury   
3468           NaN              NaT        Other  Recurrent Injury   
3469           NaN              NaT        Other  Recurrent Injury   
3470           NaN              NaT        Other  Recurrent Injury   
3471           NaN              NaT        Other  Recurrent Injury   

             Injury Date                Location OSIICs  \
2176 2021-02-27 03:35:51  Competition - Domestic    AA1   
2727 2021-04-27 09:37:43  Competition - Domestic    TZ1   
3466 2021-03-27 04:11:17  Competition - Domestic    KZZ   
3467 2021-06-03 00:45:03                   Other    NaN   
3468 2021-08-04 00:52:10                   Other    NaN   
3469 2021-08-04 00:52:14                   Other    NaN   
3470 2021-08-04 00:52:31                   Other    NaN   
3471 2021-08-04 00:52:45                   Other    NaN   

                           Onset Past Injury       Reoccurance  \
2176   Repetitive - Sudden Onset         yes    Primary Injury   
2727                       Acute          no    Primary Injury   
3466                       Acute          no  Secondary Injury   
3467  Repetitive - Gradual Onset         yes    Primary Injury   
3468  Repetitive - Gradual Onset         yes    Primary Injury   
3469  Repetitive - Gradual Onset         yes    Primary Injury   
3470  Repetitive - Gradual Onset         yes    Primary Injury   
3471  Repetitive - Gradual Onset         yes    Primary Injury   

             Return Date   Side Surgery                      u_id  \
2176 2021-03-12 03:35:51  Right      no  5f0592e2239906121f930929   
2727 2021-04-28 09:37:43   Left      no  5f0592e2239906121f930929   
3466 2021-04-01 04:11:17  Right      no  5f0592e2239906121f930929   
3467 2021-09-15 00:45:03  Right     yes  5f0592e2239906121f930929   
3468 2021-08-04 00:52:10  Right     yes  5f0592e2239906121f930929   
3469 2021-08-04 00:52:14  Right     yes  5f0592e2239906121f930929   
3470 2021-08-04 00:52:31  Right     yes  5f0592e2239906121f930929   
3471 2021-08-04 00:52:45  Right     yes  5f0592e2239906121f930929   

     FormattedInjuryDate FormattedReturnDate FormattedInjuryDate_dt  \
2176          2021-02-27          2021-03-12             2021-02-27   
2727          2021-04-27          2021-04-28             2021-04-27   
3466          2021-03-27          2021-04-01        

In [17]:
outer_df['player_id'].fillna(outer_df['u_id'], inplace=True)
outer_df['formatteddate'].fillna(outer_df['FormattedInjuryDate'], inplace=True)
outer_df['formatteddate_dt'] = pd.to_datetime(outer_df['formatteddate'])

fill_zero_cols = ["acute","acwr","chronic","duration","load","rpe"]
fill_none_cols = ['condition','type']

for col in outer_df.columns:
    if col in fill_zero_cols:
        outer_df[col] = outer_df[col].fillna(0)
    elif col in fill_none_cols:
        outer_df[col] = outer_df[col].fillna('None')
    else:
        outer_df[col] = outer_df[col]

In [18]:
outer_df[outer_df['u_id']=='5f0592e2239906121f930929']

acute  acwr  chronic condition date  duration  load  rpe  type  \
5297    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5301    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5305    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5308    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5311    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5312    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5313    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5314    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   

                     player_id name formatteddate formatteddate_dt  \
5297  5f0592e2239906121f930929  NaN    2021-02-27       2021-02-27   
5301  5f0592e2239906121f930929  NaN    2021-03-27       2021-03-27   
5305  5f0592e2239906121f930929  NaN    2021-04-27       2021-04-27   
5308  5f0592e2239906121f930929  NaN    2021-06-03       2021-06-03   
5311  5f0592e2239906121f930929  NaN    2021-08-04       2021-08-04   
5312  5f0592e2239906121f930929  NaN    2021-08-04       2021-08-04   
5313  5f0592e2239906121f930929  NaN    2021-08-04       2021-08-04   
5314  5f0592e2239906121f930929  NaN    2021-08-04       2021-08-04   

         Activity    Classification         Injury Date  \
5297  Competition  Recurrent Injury 2021-02-27 03:35:51   
5301  Competition        New Injury 2021-03-27 04:11:17   
5305  Competition        New Injury 2021-04-27 09:37:43   
5308        Other  Recurrent Injury 2021-06-03 00:45:03   
5311        Other  Recurrent Injury 2021-08-04 00:52:10   
5312        Other  Recurrent Injury 2021-08-04 00:52:14   
5313        Other  Recurrent Injury 2021-08-04 00:52:31   
5314        Other  Recurrent Injury 2021-08-04 00:52:45   

                    Location OSIICs                       Onset Past Injury  \
5297  Competition - Domestic    AA1   Repetitive - Sudden Onset         yes   
5301  Competition - Domestic    KZZ                       Acute          no   
5305  Competition - Domestic    TZ1                       Acute          no   
5308                   Other    NaN  Repetitive - Gradual Onset         yes   
5311                   Other    NaN  Repetitive - Gradual Onset         yes   
5312                   Other    NaN  Repetitive - Gradual Onset         yes   
5313                   Other    NaN  Repetitive - Gradual Onset         yes   
5314                   Other    NaN  Repetitive - Gradual Onset         yes   

           Reoccurance         Return Date   Side Surgery  \
5297    Primary Injury 2021-03-12 03:35:51  Right      no   
5301  Secondary Injury 2021-04-01 04:11:17  Right      no   
5305    Primary Injury 2021-04-28 09:37:43   Left      no   
5308    Primary Injury 2021-09-15 00:45:03  Right     yes   
5311    Primary Injury 2021-08-04 00:52:10  Right     yes   
5312    Primary Injury 2021-08-04 00:52:14  Right     yes   
5313    Primary Injury 2021-08-04 00:52:31  Right     yes   
5314    Primary Injury 2021-08-04 00:52:45  Right     yes   

                          u_id FormattedInjuryDate FormattedReturnDate  \
5297  5f0592e2239906121f930929          2021-02-27          2021-03-12   
5301  5f0592e2239906121f930929          2021-03-27          2021-04-01   
5305  5f0592e2239906121f930929          2021-04-27          2021-04-28   
5308  5f0592e2239906121f930929          2021-06-03          2021-09-15   
5311  5f0592e2239906121f930929          2021-08-04          2021-08-04   
5312  5f0592e2239906121f930929          2021-08-04          2021-08-04   
5313  5f0592e2239906121f930929          2021-08-04          2021-08-04   
5314  5f0592e2239906121f930929          2021-08-04          2021-08-04   

     FormattedInjuryDate_dt FormattedReturnDate_dt  
5297             2021-02-27             2021-03-12  
5301             2021-03-27             2021-04-01  
5305             2021-04-27             2021-04-28  
5308             2021-06-03             2021-09-15  


In [19]:
outer_df["injury?"] = outer_df.apply(lambda row: 1 
                                 if ((row['player_id'] == row['u_id']) and (row['formatteddate'] == row['FormattedInjuryDate']))
                                 else 0,
                                axis = 1)

In [20]:
outer_df.shape

(5333, 30)

In [21]:
outer_df[outer_df["injury?"]==1].shape

(41, 30)

In [22]:
injured_exposure = outer_df[outer_df["injury?"]==1].sort_values(by=['formatteddate'])
injured_exposure

acute  acwr  chronic condition date  duration  load  rpe  type  \
5292    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5293    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5294    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5295    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5296    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5297    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5298    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5299    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5300    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5301    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5302    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5303    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5304    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5305    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5306    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5307    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5308    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5309    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5310    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5314    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5313    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5312    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5311    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5315    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5316    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5317    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5318    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5319    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5320    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5321    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5322    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5323    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5324    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5325    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5326    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5327    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5328    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5329    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5330    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5331    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   
5332    0.0   0.0      0.0      None  NaT       0.0   0.0  0.0  None   

                     player_id name formatteddate formatteddate_dt  \
5292  5f059355c37cc79a7d6a6caa  NaN    2020-11-02       2020-11-02   
5293  5f014aa4b8bec1cf08f7ca0f  NaN    2020-11-22       2020-11-22   
5294  5f0593d9c37cc79a7d6a6cae  NaN    2020-12-21       2020-12-21   
5295  5f0593d9c37cc79a7d6a6cae  NaN    2021-01-25       2021-01-25   
5296  5f059326c37cc79a7d6a6ca9  NaN    2021-02-01       2021-02-01   
5297  5f0592e2239906121f930929  NaN    2021-02-27       2021-02-27   
5298  5f0593f1c37cc79a7d6a6caf  NaN    2021-03-10       2021-03-10   
5299  5f05939a239906121f930930  NaN    2021-03-17       2021-03-17   
5300  5f05939a239906121f930930  NaN    2021-03-19       2021-03-19   
5301  5f0592e2239906121f930929  NaN    2021-03-27       2021-03-27   
5302  5f86fa4805bc5268fb4a00a5  NaN    2021-04-05       2021-04-05   
5303  5f0593d9c37cc79a7d6a6cae  NaN    2021-04-10       2021-04-10   
5304  5f86fa4805bc5268fb4a00a5  NaN    2021-04-23       2021-04-23   
5

In [23]:
outer_df.sort_values(by=['formatteddate']).to_csv('exposure_injury_all_updated.csv', header=True, index=False, encoding = 'utf-8')

# Some players' exposure "type" is different from injury "activity" :

# Read the combined dataset and deal with anomalies

In [24]:
injury_exposure = pd.read_csv('exposure_injury_all_updated.csv')

In [25]:
injury_exposure.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5333 entries, 0 to 5332
Data columns (total 30 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   acute                   5333 non-null   float64
 1   acwr                    5333 non-null   float64
 2   chronic                 5333 non-null   float64
 3   condition               5333 non-null   object 
 4   date                    5292 non-null   object 
 5   duration                5333 non-null   float64
 6   load                    5333 non-null   float64
 7   rpe                     5333 non-null   float64
 8   type                    5333 non-null   object 
 9   player_id               5333 non-null   object 
 10  name                    5292 non-null   object 
 11  formatteddate           5333 non-null   object 
 12  formatteddate_dt        5333 non-null   object 
 13  Activity                40 non-null     object 
 14  Classification          41 non-null     

In [26]:
injury_exposure = injury_exposure.drop(columns = ["date", "formatteddate_dt","Injury Date", "Return Date",
                                                  "u_id", "FormattedInjuryDate_dt","FormattedReturnDate_dt"])
injury_exposure.rename(columns = {"Reoccurance":"Reoccurence"})

cols = ["formatteddate","FormattedInjuryDate","FormattedReturnDate"]
for col in cols:
    injury_exposure[col] = pd.to_datetime(injury_exposure[col])

In [27]:
injury_exposure.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5333 entries, 0 to 5332
Data columns (total 23 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   acute                5333 non-null   float64       
 1   acwr                 5333 non-null   float64       
 2   chronic              5333 non-null   float64       
 3   condition            5333 non-null   object        
 4   duration             5333 non-null   float64       
 5   load                 5333 non-null   float64       
 6   rpe                  5333 non-null   float64       
 7   type                 5333 non-null   object        
 8   player_id            5333 non-null   object        
 9   name                 5292 non-null   object        
 10  formatteddate        5333 non-null   datetime64[ns]
 11  Activity             40 non-null     object        
 12  Classification       41 non-null     object        
 13  Location             39 non-null 

In [28]:
injury1_exposure = injury_exposure[injury_exposure["injury?"] == 1]

In [29]:
injury1_exposure.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 41 entries, 1033 to 5185
Data columns (total 23 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   acute                41 non-null     float64       
 1   acwr                 41 non-null     float64       
 2   chronic              41 non-null     float64       
 3   condition            41 non-null     object        
 4   duration             41 non-null     float64       
 5   load                 41 non-null     float64       
 6   rpe                  41 non-null     float64       
 7   type                 41 non-null     object        
 8   player_id            41 non-null     object        
 9   name                 0 non-null      object        
 10  formatteddate        41 non-null     datetime64[ns]
 11  Activity             40 non-null     object        
 12  Classification       41 non-null     object        
 13  Location             39 non-null

In [30]:
players_inj_lst = []
inj_players = set(injury1_exposure["player_id"])
for p in inj_players:
    df = injury_exposure[injury_exposure["player_id"] == p].reset_index()
    players_inj_lst.append(df)
   

In [31]:
inj_players

{'5f014aa4b8bec1cf08f7ca0f',
 '5f0592cc239906121f930928',
 '5f0592e2239906121f930929',
 '5f059326c37cc79a7d6a6ca9',
 '5f059355c37cc79a7d6a6caa',
 '5f059378239906121f93092e',
 '5f059388239906121f93092f',
 '5f05939a239906121f930930',
 '5f0593d9c37cc79a7d6a6cae',
 '5f0593f1c37cc79a7d6a6caf',
 '5f86fa4805bc5268fb4a00a5',
 '60f253c0854df5b9da1bac54',
 '60f25487854df5b9da1bac55',
 '6107d0a36f7b01ca9c0f6571',
 '61139a2f859c5efc737749ba',
 '61162b72840a022569af263d',
 '611a41e057d5db652811c0f3'}

In [32]:
players_inj_lst[3][players_inj_lst[3]["injury?"]==1]

index  acute  acwr  chronic condition  duration  load  rpe  type  \
89   4319    0.0   0.0      0.0      None       0.0   0.0  0.0  None   

                   player_id name formatteddate     Activity  \
89  60f253c0854df5b9da1bac54  NaN    2021-11-20  Competition   

      Classification                Location OSIICs  Onset Past Injury  \
89  Recurrent Injury  Competition - Domestic    NaN  Acute          no   

       Reoccurance  Side Surgery FormattedInjuryDate FormattedReturnDate  \
89  Primary Injury  Left      no          2021-11-20          2021-11-27   

    injury?  
89        1

In [33]:
pd.set_option('display.max_rows', None)
kota = players_inj_lst[3]
kota

index       acute      acwr     chronic         condition  duration  \
0     2855  450.000000  1.000000  450.000000  Artificial (Dry)      75.0   
1     2876  540.000000  1.137255  474.827586       Grass (Wet)      90.0   
2     2889  502.500000  1.071480  468.977408  Artificial (Dry)      65.0   
3     2903  511.875000  1.080189  473.875518  Artificial (Dry)      60.0   
4     2914  471.406250  1.013053  465.332379  Artificial (Dry)      70.0   
5     2929  432.304688  0.950194  454.964628  Artificial (Dry)      35.0   
6     2950  373.628540  0.889729  419.935167       Grass (Dry)      85.0   
7     2958  460.221405  1.044464  440.629293  Artificial (Dry)      80.0   
8     2986  427.666054  0.987682  432.999687  Artificial (Dry)      55.0   
9     2994  470.749540  1.059014  444.516950  Artificial (Wet)      60.0   
10    3013  356.097462  0.885389  402.193084  Artificial (Dry)      90.0   
11    3023  442.073097  1.045754  422.731492       Grass (Dry)      70.0   
12    3045  544.054823  1.203133  452.198285       Grass (Dry)      85.0   
13    3062  491.791117  1.107349  444.115645  Artificial (Dry)      67.0   
14    3080  290.605783  0.783423  370.943631  Artificial (Dry)      90.0   
15    3097  387.954337  0.989029  392.257864       Grass (Wet)      85.0   
16    3107  450.965753  1.101680  409.343528       Grass (Wet)      80.0   
17    3134  508.224315  1.187414  428.009492       Grass (Wet)      85.0   
18    3147  583.668236  1.284612  454.353665       Grass (Wet)      90.0   
19    3165  354.676278  0.913428  388.291508  Artificial (Dry)      85.0   
20    3175  423.507208  1.045797  404.961059  Artificial (Dry)      90.0   
21    3204  531.380406  1.218767  435.998227  Artificial (Wet)      95.0   
22    3214  492.285305  1.140100  431.791453       Grass (Dry)      75.0   
23    3225  444.213979  1.050891  422.702387  Artificial (Dry)      60.0   
24    3240  520.660484  1.169302  445.274636       Grass (Dry)      75.0   
25    3256  326.621522  0.826292  395.285624  Artificial (Dry)      45.0   
26    3274  341.216142  0.864766  394.576271  Artificial (Dry)      55.0   
27    3291  405.912106  0.993073  408.743425  Artificial (Dry)      75.0   
28    3313  394.434080  0.972994  405.381809  Artificial (Dry)      60.0   
29    3322  520.825560  1.185059  439.493408       Grass (Dry)      90.0   
30    3334  388.473283  0.968176  401.242312       Grass (Dry)      75.0   
31    3365  373.854962  0.943294  396.329050       Grass (Dry)      55.0   
32    3375  440.391222  1.065977  413.133943       Grass (Dry)      80.0   
33    3388  361.470062  0.928050  389.494226       Grass (Dry)      65.0   
34    3400  333.602547  0.878193  379.873935       Grass (Dry)      50.0   
35    3421  475.201910  1.143014  415.744698       Grass (Dry)      90.0   
36    3440  289.801074  0.790543  366.584881       Grass (Wet)      30.0   
37    3449  347.350806  0.920951  377.165234  Artificial (Dry)      65.0   
38    3468  358.013104  0.946998  378.050390       Grass (Wet)      65.0   
39    3490  343.509828  0.921759  372.667605  Artificial (Dry)      60.0   
40    3507  482.632371  1.179928  409.035356       Grass (Dry)      90.0   
41    3523  291.480709  0.809490  360.079399       Grass (Dry)      40.0   
42    3546  443.610532  1.116520  397.315302       Grass (Dry)      90.0   
43    3564  262.030924  0.753285  347.851196       Grass (Dry)      25.0   
44    3574  264.023193  0.770911  342.482148       Grass (Dry)      45.0   
45    3592  373.513046  1.040597  358.941124       Grass (Dry)      90.0   
46    3610  245.101088  0.764044  320.794387       Grass (Dry)      35.0   
47    3629  288.825816  0.881544  327.636154       Grass (Dry)      70.0   
48    3646  385.369362  1.096069  351.592281  Artificial (Dry)      75.0   
49    3660  251.933275  0.839656  300.043566       Grass (Dry)      65.0   
50    3681  290.949956  0.946213  307.488837       Grass (Wet)      68.0   
51    3706  388.659350  1.182744  328.608041       Gr

In [34]:
def label_injury(row):
    if row["injury?"]==1:
        if (row["type"].startswith("Practice")) and (row["Activity"]=="General Training"):
            return False
        elif (row["type"]=="Game") and (row["Activity"]=="Competition"):
            return False
        else:
            return True
    else:
        return False
    
    
def posix_time(dt):
    return ((dt - datetime(1970, 1, 1)) / timedelta(seconds=1))/(24*60*60)

In [35]:
def player_handler(kota):
    kota['NeedActualInjuryDate'] = kota.apply(lambda row: label_injury(row), axis=1)
    kota['daydiff'] = kota['formatteddate'].apply(posix_time)

    kota_need = kota[kota["NeedActualInjuryDate"]==True]


    #activity_lst = ['Competition', 'General Training']
    #type_lst = ['Game', 'Practice']


    kota_activity_game_idx = kota_need.index[kota_need['Activity']=='Competition'].tolist()
    kota_activity_train_idx = kota_need.index[kota_need['Activity']=='General Training'].tolist()
    kota_activity_gt_idx = kota_activity_game_idx + kota_activity_train_idx
    kota_activity_other_idx = kota_need.index[(kota_need['Activity'] != 'Competition') & 
                                          (kota_need['Activity'] != 'General Training')].tolist()

    kota_type_game_idx = kota.index[kota['type']=='Game'].tolist()
    kota_type_train_idx = kota.index[kota['type'].apply(lambda row: row.startswith('Practice'))].tolist()

    res_lst = []
    for idx in kota_activity_game_idx:
        for idx2 in kota_type_game_idx:
            if idx2 <= idx:
                res = idx2
        res_lst.append(res)
    #print(res_lst)
    for idx in kota_activity_train_idx:
        for idx2 in kota_type_train_idx:
            if idx2 <= idx:
                res = idx2
        res_lst.append(res)
    #print(res_lst)

    
    
    actual_injury_dt = kota['FormattedInjuryDate'].tolist()

    for i in range(len(kota_activity_gt_idx)):
        diff = kota.loc[kota_activity_gt_idx[i]]['daydiff'] - kota.loc[res_lst[i]]['daydiff']
        if diff <= 7:
            actual_injury_dt[kota_activity_gt_idx[i]] = kota.loc[res_lst[i]]['formatteddate']
        else:
            j = kota_activity_gt_idx[i]-1
            #print(j)
            while (kota.loc[j]['type'] == 'Rehab') or (kota.loc[j]['type'] == 'Modified') or (kota.loc[j]['formatteddate'] == kota[kota['type']=='Rehab']['formatteddate'].tolist()[0]):
                j = j - 1 
                #print(j)
            actual_injury_dt[kota_activity_gt_idx[i]] = kota.loc[j]['formatteddate']
        
    for i in range(len(kota_activity_other_idx)):
        j = kota_activity_other_idx[i]-1
        while (kota.loc[j]['type'] == 'Rehab') or (kota.loc[j]['type'] == 'Modified') or (kota.loc[j]['formatteddate'] == kota[kota['type']=='Rehab']['formatteddate'].tolist()[0]):
            j = j - 1
        actual_injury_dt[kota_activity_other_idx[i]] = kota.loc[j]['formatteddate']
               
        
    kota['actualInjuryDate'] = actual_injury_dt
    return kota

In [36]:
players_inj_lst = []
inj_players = set(injury_exposure["player_id"])
for p in inj_players:
    df = injury_exposure[injury_exposure["player_id"] == p].reset_index()
    df_new = player_handler(df)
    players_inj_lst.append(df_new)

new_players_inj = pd.concat(players_inj_lst)

In [37]:
new_players_inj

index       acute      acwr     chronic         condition  duration  \
0      857  120.000000  1.000000  120.000000  Artificial (Dry)      30.0   
1      866  225.000000  1.510417  148.965517  Artificial (Dry)      60.0   
2      871  360.000000  1.880380  191.450654  Artificial (Dry)      85.0   
3      882  450.000000  1.974530  227.902333  Artificial (Dry)      80.0   
4      888  366.875000  1.602559  228.930798  Artificial (Dry)      65.0   
5      898  335.156250  1.459141  229.694191  Artificial (Dry)      30.0   
6      908  459.156250  1.739880  263.901087  Artificial (Dry)      62.0   
7      918  434.367188  1.605624  270.528599  Artificial (Dry)      60.0   
8      930  476.525391  1.623830  293.457661  Artificial (Dry)      67.0   
9      941  419.894043  1.445615  290.460581  Artificial (Dry)      50.0   
10     951  355.420532  1.262141  281.601230       Grass (Dry)      27.0   
11     960  309.924049  1.129280  274.443873  Artificial (Dry)      55.0   
12     975  342.443037  1.197933  285.861537  Artificial (Dry)      55.0   
13     981  379.943037  1.282697  296.206364       Gym/Indoors      30.0   
14     993  462.707278  1.424535  324.812822  Artificial (Dry)      79.0   
15    1002  422.272844  1.294340  326.245597  Artificial (Dry)      72.0   
16    1014  436.704633  1.296439  336.849349  Artificial (Dry)      60.0   
17    1043  251.734767  0.866637  290.472989  Artificial (Dry)      45.0   
18    1045  241.301075  0.846899  284.923128  Artificial (Dry)      30.0   
19    1055  376.301075  1.168040  322.164507  Artificial (Dry)      60.0   
20    1066  369.725806  1.140833  324.084196  Artificial (Dry)      50.0   
21    1084  322.294355  1.025934  314.147355  Artificial (Dry)      45.0   
22    1087  476.720766  1.334195  357.309607       Grass (Dry)      94.0   
23    1095  283.155431  0.902163  313.862905  Artificial (Dry)      30.0   
24    1107  234.866573  0.787023  298.424084       Grass (Dry)      45.0   
25    1117  413.649930  1.204711  343.360354       Grass (Dry)      95.0   
26    1129  247.678086  0.820748  301.771342  Artificial (Dry)      30.0   
27    1139  290.758564  0.938158  309.925042  Artificial (Dry)      60.0   
28    1160  242.663769  0.856783  283.226643  Artificial (Dry)      60.0   
29    1169  297.997827  1.007792  295.693771  Artificial (Dry)      58.0   
30    1184  357.997827  1.146527  312.245495  Artificial (Dry)      30.0   
31    1191  388.498370  1.199755  323.814772       Grass (Dry)      60.0   
32    1202  323.623778  1.042672  310.379270  Artificial (Dry)      43.0   
33    1212  475.217833  1.345800  353.111734       Grass (Wet)      93.0   
34    1227  235.482523  0.799243  294.631935  Artificial (Dry)      35.0   
35    1241  229.111893  0.793337  288.795250  Artificial (Dry)      30.0   
36    1242  347.111893  1.080178  321.346974  Artificial (Dry)      59.0   
37    1261  390.333919  1.165012  335.047183  Artificial (Dry)      65.0   
38    1263  326.500440  1.016341  321.250825  Artificial (Dry)      45.0   
39    1278  479.875330  1.318617  363.923182       Grass (Dry)      94.0   
40    1279  284.929873  0.891532  319.595719  Artificial (Dry)      30.0   
41    1292  309.947405  0.956314  324.106359       Grass (Dry)      55.0   
42    1300  362.447405  1.070464  338.589118       Grass (Dry)      30.0   
43    1318  214.157499  0.738085  290.152922             Track      35.0   
44    1330  135.347695  0.548900  246.580014             Track      30.0   
45    1342  154.010771  0.631044  244.057254       Gym/Indoors      30.0   
46    1351  232.760771  0.875760  265.781392             Track      35.0   
47    1365  309.570578  1.087384  284.693020              Hike      90.0   
48    1370  307.177934  1.074993  285.748674       Gym/Indoors      60.0   
49    1382  290.383450  1.027566  282.593593             Track      30.0   
50    1398  193.005518  0.779777  247.513785             Track      47.0   
51    1400  214.754139  0.859862  249.754213         

In [38]:
new_players_inj[new_players_inj['NeedActualInjuryDate']==1]

index  acute  acwr  chronic condition  duration  load  rpe  type  \
142   2367    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
159   2539    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
21    3315    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
52    3876    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
32    3547    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
124   1033    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
285   2723    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   2859    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
300   2860    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
302   3431    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
25    3693    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
144   1446    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
166   1720    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
233   2420    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
277   2896    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   4460    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
86    4318    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
207   2123    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
296   3144    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
341   3875    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
343   3890    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
178   2192    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
179   2203    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
251   3125    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
172   1780    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
286   3265    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
387   5013    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
131   1221    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
89    4319    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
198   2028    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
221   2283    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
249   2560    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
277   2845    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
278   2877    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
279   2878    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
280   2879    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
281   2880    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
244   2755    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
270   3126    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
6     2971    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
125   5185    0.0   0.0      0.0      None       0.0   0.0  0.0  None   

                    player_id name formatteddate               Activity  \
142  5f86fa4805bc5268fb4a00a5  NaN    2021-04-05            Competition   
159  5f86fa4805bc5268fb4a00a5  NaN    2021-04-23            Competition   
21   61139a2f859c5efc737749ba  NaN    2021-09-10                    NaN   
52   61139a2f859c5efc737749ba  NaN    2021-10-24            Competition   
32   611a41e057d5db652811c0f3  NaN    2021-09-30       General Training   
124  5f059355c37cc79a7d6a6caa  NaN    2020-11-02       General Training   
285  5f059355c37cc79a7d6a6caa  NaN    2021-05-16            Competition   
299  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
300  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
302  5f059388239906121f93092f  NaN    2021-09-21       General Training   
25   61162b72840a022569af263d  NaN    2021-10-14            Competition   
144  5f0593d9c37cc79a7d6a6cae  NaN    

In [39]:
# deal with the special cases
new_players_inj.drop([277,278,279],inplace=True)
new_players_inj.at[276, 'actualInjuryDate'] = '2021-05-30'
new_players_inj[new_players_inj['NeedActualInjuryDate']==1]

index  acute  acwr  chronic condition  duration  load  rpe  type  \
142   2367    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
159   2539    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
21    3315    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
52    3876    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
32    3547    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
124   1033    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
285   2723    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   2859    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
300   2860    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
302   3431    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
25    3693    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
144   1446    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
166   1720    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
233   2420    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   4460    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
86    4318    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
207   2123    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
296   3144    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
341   3875    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
343   3890    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
178   2192    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
179   2203    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
251   3125    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
172   1780    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
286   3265    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
387   5013    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
131   1221    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
89    4319    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
198   2028    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
221   2283    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
249   2560    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
280   2879    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
281   2880    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
244   2755    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
270   3126    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
6     2971    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
125   5185    0.0   0.0      0.0      None       0.0   0.0  0.0  None   

                    player_id name formatteddate               Activity  \
142  5f86fa4805bc5268fb4a00a5  NaN    2021-04-05            Competition   
159  5f86fa4805bc5268fb4a00a5  NaN    2021-04-23            Competition   
21   61139a2f859c5efc737749ba  NaN    2021-09-10                    NaN   
52   61139a2f859c5efc737749ba  NaN    2021-10-24            Competition   
32   611a41e057d5db652811c0f3  NaN    2021-09-30       General Training   
124  5f059355c37cc79a7d6a6caa  NaN    2020-11-02       General Training   
285  5f059355c37cc79a7d6a6caa  NaN    2021-05-16            Competition   
299  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
300  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
302  5f059388239906121f93092f  NaN    2021-09-21       General Training   
25   61162b72840a022569af263d  NaN    2021-10-14            Competition   
144  5f0593d9c37cc79a7d6a6cae  NaN    2020-12-21       General Training   
166  5f0593d9c37cc79a7d6a6cae  NaN    2021-01-25       General Training   
233  5f0593d9c37cc79a7d6a6cae  NaN    2021-04-10  Not Related to Sports   
299  5f059378239906121f93092e  NaN    2021-11-29       General Training   
86   60f25487854df5b9da1bac55 

In [40]:
new_players_inj[new_players_inj['injury?']==1]
#length = 25

index  acute  acwr  chronic condition  duration  load  rpe  type  \
142   2367    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
159   2539    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
21    3315    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
52    3876    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
32    3547    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
124   1033    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
285   2723    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   2859    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
300   2860    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
302   3431    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
25    3693    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
144   1446    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
166   1720    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
233   2420    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
299   4460    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
86    4318    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
207   2123    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
296   3144    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
341   3875    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
343   3890    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
178   2192    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
179   2203    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
251   3125    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
172   1780    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
286   3265    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
387   5013    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
131   1221    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
89    4319    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
198   2028    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
221   2283    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
249   2560    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
280   2879    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
281   2880    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
244   2755    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
270   3126    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
6     2971    0.0   0.0      0.0      None       0.0   0.0  0.0  None   
125   5185    0.0   0.0      0.0      None       0.0   0.0  0.0  None   

                    player_id name formatteddate               Activity  \
142  5f86fa4805bc5268fb4a00a5  NaN    2021-04-05            Competition   
159  5f86fa4805bc5268fb4a00a5  NaN    2021-04-23            Competition   
21   61139a2f859c5efc737749ba  NaN    2021-09-10                    NaN   
52   61139a2f859c5efc737749ba  NaN    2021-10-24            Competition   
32   611a41e057d5db652811c0f3  NaN    2021-09-30       General Training   
124  5f059355c37cc79a7d6a6caa  NaN    2020-11-02       General Training   
285  5f059355c37cc79a7d6a6caa  NaN    2021-05-16            Competition   
299  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
300  5f059355c37cc79a7d6a6caa  NaN    2021-08-03       General Training   
302  5f059388239906121f93092f  NaN    2021-09-21       General Training   
25   61162b72840a022569af263d  NaN    2021-10-14            Competition   
144  5f0593d9c37cc79a7d6a6cae  NaN    2020-12-21       General Training   
166  5f0593d9c37cc79a7d6a6cae  NaN    2021-01-25       General Training   
233  5f0593d9c37cc79a7d6a6cae  NaN    2021-04-10  Not Related to Sports   
299  5f059378239906121f93092e  NaN    2021-11-29       General Training   
86   60f25487854df5b9da1bac55 

In [41]:
player = set(new_players_inj['player_id'])
print(player)
print(len(player))
injured_player = set(new_players_inj[new_players_inj['injury?']==1]['player_id'])
print(injured_player)

{'5f86fa4805bc5268fb4a00a5', '60f254ada1b3ec106cc401d9', '61139a2f859c5efc737749ba', '60f254d8a1b3ec106cc401da', '611a41e057d5db652811c0f3', '5f059355c37cc79a7d6a6caa', '5f059388239906121f93092f', '61162b72840a022569af263d', '60f254fb854df5b9da1bac56', '5f0593d9c37cc79a7d6a6cae', '5f059378239906121f93092e', '60f25487854df5b9da1bac55', '5f0593f1c37cc79a7d6a6caf', '5f05939a239906121f930930', '5f059326c37cc79a7d6a6ca9', '5f014aa4b8bec1cf08f7ca0f', '6153f4f14983cc4b427f2af2', '60f253c0854df5b9da1bac54', '5f0592e2239906121f930929', '5f0592cc239906121f930928', '6107d0a36f7b01ca9c0f6571'}
21
{'5f86fa4805bc5268fb4a00a5', '5f014aa4b8bec1cf08f7ca0f', '5f0593d9c37cc79a7d6a6cae', '60f253c0854df5b9da1bac54', '5f0592e2239906121f930929', '611a41e057d5db652811c0f3', '5f059378239906121f93092e', '5f059355c37cc79a7d6a6caa', '6107d0a36f7b01ca9c0f6571', '5f0592cc239906121f930928', '5f059388239906121f93092f', '60f25487854df5b9da1bac55', '5f0593f1c37cc79a7d6a6caf', '61139a2f859c5efc737749ba', '5f05939a239906

In [20]:
new_players_inj.to_csv('cleaned_player_inj.csv', header=True, index=False, encoding = 'utf-8')